![image info](https://raw.githubusercontent.com/albahnsen/MIAD_ML_and_NLP/main/images/banner_1.png)

# Taller: Construcción e implementación de modelos Bagging, Random Forest y XGBoost

En este taller podrán poner en práctica sus conocimientos sobre la construcción e implementación de modelos de Bagging, Random Forest y XGBoost. El taller está constituido por 8 puntos, en los cuales deberan seguir las intrucciones de cada numeral para su desarrollo.

## Datos predicción precio de automóviles

En este taller se usará el conjunto de datos de Car Listings de Kaggle donde cada observación representa el precio de un automóvil teniendo en cuenta distintas variables como año, marca, modelo, entre otras. El objetivo es predecir el precio del automóvil. Para más detalles puede visitar el siguiente enlace: [datos](https://www.kaggle.com/jpayne/852k-used-car-listings).

In [1]:
import warnings
warnings.filterwarnings('ignore')

In [6]:
# Importación de librerías
%matplotlib inline
import pandas as pd
import numpy as np

# Lectura de la información de archivo .csv
data = pd.read_csv('https://raw.githubusercontent.com/albahnsen/MIAD_ML_and_NLP/main/datasets/dataTrain_carListings.zip')

# Preprocesamiento de datos para el taller
data = data.loc[data['Model'].str.contains('Camry')].drop(['Make', 'State'], axis=1)
data = data.join(pd.get_dummies(data['Model'], prefix='M'))
data = data.drop(['Model'], axis=1)

# Visualización dataset
data.head()

Price  Year  Mileage  M_Camry  M_Camry4dr  M_CamryBase  M_CamryL  \
7    21995  2014     6480        0           0            0         1   
11   13995  2014    39972        0           0            0         0   
167  17941  2016    18989        0           0            0         0   
225  12493  2014    51330        0           0            0         1   
270   7994  2007   116065        0           1            0         0   

     M_CamryLE  M_CamrySE  M_CamryXLE  
7            0          0           0  
11           1          0           0  
167          0          1           0  
225          0          0           0  
270          0          0           0

In [7]:
# Separación de variables predictoras (X) y variable de interés (y)
y = data['Price']
X = data.drop(['Price'], axis=1)

In [8]:
# Separación de datos en set de entrenamiento y test
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=42)

### Punto 1 - Árbol de decisión manual

En la celda 1 creen un árbol de decisión **manualmente**  que considere los set de entrenamiento y test definidos anteriormente y presenten el RMSE y MAE del modelo en el set de test.

In [9]:
# Definición de la función que calcula el gini index
def gini(y_train):
    if y.shape[0] == 0:
        return 0
    else:
        return 1 - (y_train.mean()**2 + (1 - y_train.mean())**2)
# Definición de la función gini_imputiry para calular la ganancia de una variable predictora j dado el punto de corte k
def gini_impurity(X_col, y, split):
    
    filter_l = X_col < split
    y_l = y.loc[filter_l]
    y_r = y.loc[~filter_l]
    
    n_l = y_l.shape[0]
    n_r = y_r.shape[0]
    
    gini_y = gini(y)
    gini_l = gini(y_l)
    gini_r = gini(y_r)
    
    gini_impurity_ = gini_y - (n_l / (n_l + n_r) * gini_l + n_r / (n_l + n_r) * gini_r)
    
    return gini_impurity_

# Definición de la función best_split para calcular cuál es la mejor variable y punto de cortepara hacer la bifurcación del árbol
def best_split(X_train, y_train, num_pct=10):
    
    features = range(X_train.shape[1])
    
    best_split = [0, 0, 0]  # j, split, gain
    
    # Para todas las varibles 
    for j in features:
        
        splits = np.percentile(X_train.iloc[:, j], np.arange(0, 100, 100.0 / (num_pct+1)).tolist())
        splits = np.unique(splits)[1:]
        
        # Para cada partición
        for split in splits:
            gain = gini_impurity(X_train.iloc[:, j], y_train, split)
                        
            if gain > best_split[2]:
                best_split = [j, split, gain]
    
    return best_split

X_train = X_train.reset_index(drop=True)
X_test = X_test.reset_index(drop=True)
y_train = y_train.reset_index(drop=True)
y_test = y_test.reset_index(drop=True)

def predict(X, tree):
    if 'y_pred' in tree:
        return tree['y_pred']
    j, split = tree['split']
    if X.iloc[j] < split:
        return predict(X, tree['sl'])
    else:
        return predict(X, tree['sr'])


# Definición de la función tree_grow para hacer un crecimiento recursivo del árbol
def tree_grow(X_train, y_train, X_test, y_test, level=0, min_gain=0.001, max_depth=None, num_pct=10):
    
    # Si solo es una observación
    if X_train.shape[0] == 1:
        tree = dict(y_pred=y_train.iloc[:1].values[0], y_prob=0.5, level=level, split=-1, n_samples=1, gain=0)
        return tree
    
    # Calcular la mejor división
    j, split, gain = best_split(X_train, y_train, num_pct)
    
    # Guardar el árbol y estimar la predicción
    y_pred = int(y_train.mean() >= 0.5) 
    y_prob = (y_train.sum() + 1.0) / (y_train.shape[0] + 2.0)  # Corrección Laplace 
    
    tree = dict(y_pred=y_pred, y_prob=y_prob, level=level, split=-1, n_samples=X_train.shape[0], gain=gain)
    
    # Revisar el criterio de parada 
    if gain < min_gain:
        return tree
    if max_depth is not None:
        if level >= max_depth:
            return tree
    
    # Continuar creando la partición
    filter_l = X_train.iloc[:, j] < split
    X_train_l, y_train_l = X_train.loc[filter_l].reset_index(drop=True), y_train.loc[filter_l].reset_index(drop=True)
    X_train_r, y_train_r = X_train.loc[~filter_l].reset_index(drop=True), y_train.loc[~filter_l].reset_index(drop=True)
    tree['split'] = [j, split]
    
    # Selección de filas correspondientes al conjunto de prueba
    filter_test_l = X_test.iloc[:, j] < split
    X_test_l, y_test_l = X_test.loc[filter_test_l].reset_index(drop=True), y_test.loc[filter_test_l].reset_index(drop=True)
    X_test_r, y_test_r = X_test.loc[~filter_test_l].reset_index(drop=True), y_test.loc[~filter_test_l].reset_index(drop=True)

    # Siguiente iteración para cada partición
    tree['sl'] = tree_grow(X_train_l, y_train_l, X_test_l, y_test_l, level + 1, min_gain=min_gain, max_depth=max_depth, num_pct=num_pct)
    tree['sr'] = tree_grow(X_train_r, y_train_r, X_test_r, y_test_r, level + 1, min_gain=min_gain, max_depth=max_depth, num_pct=num_pct)
    
    # Calcular RMSE y MAE del conjunto de prueba
    y_pred_test = predict(X_test, tree)
    RMSE = np.sqrt(np.mean((y_test - y_pred_test)**2))
    MAE = np.mean(np.abs(y_test - y_pred_test))
    tree['RMSE'] = RMSE
    tree['MAE'] = MAE
    
    return tree

tree_grow(X_train, y_train, X_test, y_test, level=0, min_gain=0.001, max_depth=None, num_pct=10)


{'y_pred': 1,
 'y_prob': 14503.947817432107,
 'level': 0,
 'split': [0, 2014.0],
 'n_samples': 7031,
 'gain': 17412158.538160443,
 'sl': {'y_pred': 1,
  'y_prob': 10225.920774647888,
  'level': 1,
  'split': [0, 2012.0],
  'n_samples': 2270,
  'gain': 8039318.299921066,
  'sl': {'y_pred': 1,
   'y_prob': 8725.304318026045,
   'level': 2,
   'split': [1, 97798.72727272728],
   'n_samples': 1457,
   'gain': 2218560.9485784173,
   'sl': {'y_pred': 1,
    'y_prob': 9861.673192771084,
    'level': 3,
    'split': [0, 2008.0],
    'n_samples': 662,
    'gain': 1805269.9185358882,
    'sl': {'y_pred': 1,
     'y_prob': 8335.705583756346,
     'level': 4,
     'split': [0, 2006.0],
     'n_samples': 195,
     'gain': 673731.5916494727,
     'sl': {'y_pred': 1,
      'y_prob': 7398.144927536232,
      'level': 5,
      'split': [1, 51260.0],
      'n_samples': 67,
      'gain': 562576.9282495081,
      'sl': {'y_pred': 1,
       'y_prob': 7503.857142857143,
       'level': 6,
       'split': [1

### Punto 2 - Bagging manual

En la celda 2 creen un modelo bagging **manualmente** con 10 árboles de regresión y comenten sobre el desempeño del modelo.

In [ ]:
# Celda 2


### Punto 3 - Bagging con librería

En la celda 3, con la librería sklearn, entrenen un modelo bagging con 10 árboles de regresión y el parámetro `max_features` igual a `log(n_features)` y comenten sobre el desempeño del modelo.

In [ ]:
# Celda 3


### Punto 4 - Random forest con librería

En la celda 4, usando la librería sklearn entrenen un modelo de Randon Forest para regresión  y comenten sobre el desempeño del modelo.

In [ ]:
# Celda 4


### Punto 5 - Calibración de parámetros Random forest

En la celda 5, calibren los parámetros max_depth, max_features y n_estimators del modelo de Randon Forest para regresión, comenten sobre el desempeño del modelo y describan cómo cada parámetro afecta el desempeño del modelo.

In [ ]:
# Celda 5


### Punto 6 - XGBoost con librería

En la celda 6 implementen un modelo XGBoost de regresión con la librería sklearn y comenten sobre el desempeño del modelo.

In [ ]:
# Celda 6


### Punto 7 - Calibración de parámetros XGBoost

En la celda 7 calibren los parámetros learning rate, gamma y colsample_bytree del modelo XGBoost para regresión, comenten sobre el desempeño del modelo y describan cómo cada parámetro afecta el desempeño del modelo.

In [ ]:
# Celda 7


### Punto 8 - Comparación y análisis de resultados
En la celda 8 comparen los resultados obtenidos de los diferentes modelos (random forest y XGBoost) y comenten las ventajas del mejor modelo y las desventajas del modelo con el menor desempeño.

In [ ]:
# Celda 8
